In [16]:
#import
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
import pandas as pd
import regex as re

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [1]:
import scrapy
from scrapy.crawler import CrawlerProcess
import json

class AraigneeSante(scrapy.Spider):  # Classe de l'araignée pour extraire des informations liées à la santé
    name = 'sante'
    start_urls = ['https://www.webteb.com/diseases']

    def parse(self, response):  # Fonction pour analyser la page principale des maladies
        elements = response.css('div.content.acc-content ul.list li')
        for element in elements:
            type_maladie = element.css('a::text').get().strip()  # Récupérer le type de maladie
            lien_maladie = element.css('a::attr(href)').get()  # Récupérer le lien de la maladie
            lien_base = lien_maladie.split('/diseases')[0]  # Obtenir le lien de base
            lien_complet = response.urljoin(lien_base + "/diseases/")  # Construire le lien complet
            yield scrapy.Request(
                url=lien_complet, 
                callback=self.parse_liste_maladies, 
                meta={'type_maladie': type_maladie, 'lien': lien_complet}
            )

    def parse_liste_maladies(self, response):  # Fonction pour analyser la liste des maladies
        type_maladie = response.meta['type_maladie']  # Récupérer le type de maladie depuis les métadonnées
        maladies = response.css('div.search-result.border div.content')
        for maladie in maladies:
            nom_maladie = maladie.css('a.bold span::text').get().strip()  # Nom de la maladie
            lien_maladie = maladie.css('a.bold::attr(href)').get()  # Lien de la maladie
            lien_complet_maladie = response.urljoin(lien_maladie)  # Lien complet vers la maladie
            yield scrapy.Request(
                url=lien_complet_maladie, 
                callback=self.parse_details_maladie, 
                meta={'type_maladie': type_maladie, 'nom_maladie': nom_maladie}
            )

    def parse_details_maladie(self, response):  # Fonction pour extraire les détails de chaque maladie
        type_maladie = response.meta['type_maladie']
        nom_maladie = response.meta['nom_maladie']
        
        # Extraction des données pour chaque section
        description = response.css('div#description').xpath('string()').get().strip()  # Description générale
        titre_symptomes = response.css('div#symptoms > h2::text').get()  # Titre des symptômes
        symptomes = '\n'.join(response.css('div#symptoms ul li::text').getall())  # Liste des symptômes
        titre_causes_facteurs = response.css('div#causesandriskfactors > h2::text').get()  # Causes et facteurs de risque
        causes_facteurs = '\n'.join(response.css('div#causesandriskfactors ul li::text').getall())
        titre_complications = response.css('div#complications > h2::text').get()  # Complications possibles
        complications = '\n'.join(response.css('div#complications ul li::text').getall())
        titre_diagnostic = response.css('div#diagnosis > h2::text').get()  # Diagnostic
        diagnostic = '\n'.join(response.css('div#diagnosis ul li::text').getall())
        titre_traitements = response.css('div#treatementsanddrugs > h2::text').get()  # Traitements et médicaments
        traitements = '\n'.join(response.css('div#treatementsanddrugs p::text').getall())
        titre_prevention = response.css('div#prevention > h2::text').get()  # Prévention
        prevention = '\n'.join(response.css('div#prevention ul li::text').getall())

        contenu = f"{type_maladie}\n{nom_maladie}\n{description}\n\n{titre_symptomes}:\n{symptomes}\n\n{titre_causes_facteurs}:\n{causes_facteurs}\n\n{titre_complications}:\n{complications}\n\n{titre_diagnostic}:\n{diagnostic}\n\n{titre_traitements}:\n{traitements}\n\n{titre_prevention}:\n{prevention}"

        yield {
            'type_maladie': type_maladie,
            'nom_maladie': nom_maladie,
            'contenu': contenu
        }

# Créer un processus pour exécuter l'araignée
processus = CrawlerProcess(settings={
    'FEEDS': {
        'details_maladies.json': {  # Nom du fichier de sortie
            'format': 'json',
            'encoding': 'utf8',
            'overwrite': True,
        },
    },
})

# Exécuter l'araignée
processus.crawl(AraigneeSante)
processus.start()

# Charger et afficher les données depuis le fichier JSON
with open('details_maladies.json', 'r', encoding='utf8') as f:
    details_maladies = json.load(f)

# Afficher les données extraites
for item in details_maladies:
    print(item['contenu'])


2024-12-03 21:46:52 [scrapy.utils.log] INFO: Scrapy 2.11.2 started (bot: scrapybot)
2024-12-03 21:46:52 [scrapy.utils.log] INFO: Versions: lxml 5.2.2.0, libxml2 2.11.7, cssselect 1.2.0, parsel 1.9.1, w3lib 2.1.2, Twisted 24.3.0, Python 3.12.3 (tags/v3.12.3:f6650f9, Apr  9 2024, 14:05:25) [MSC v.1938 64 bit (AMD64)], pyOpenSSL 24.1.0 (OpenSSL 3.2.1 30 Jan 2024), cryptography 42.0.7, Platform Windows-10-10.0.19045-SP0
2024-12-03 21:46:52 [scrapy.addons] INFO: Enabled addons:
[]
2024-12-03 21:46:52 [py.warnings] WARNING: c:\Users\HP\AppData\Local\Programs\Python\Python312\Lib\site-packages\scrapy\utils\request.py:254: ScrapyDeprecationWarning: '2.6' is a deprecated value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting.

It is also the default value. In other words, it is normal to get this warning if you have not defined a value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting. This is so for backward compatibility reasons, but it will change in a future version of Scrapy.

S

تسوس الأسنان
تسوس الاسنان
تسوس الأسنان هو حالة تكون فيها أجزاء من الأسنان مصابة بالتعفن الذي قد يتطور إلى ثقوب صغيرة أو كبيرة بشكل تدريجي.

يُشكل تسوس الأسنان إحدى المشكلات الصحية الأكثر انتشارًا في مختلف أنحاء العالم، وهو منتشر بالدرجة الأولى بين الأطفال والمراهقين، إلا أن كل إنسان في فمه أسنان قد يُصاب بالتسوس، وفي حال عدم معالجة تسوس الأسنان فإن الثقوب قد تكبر وتتسع ممّا يُسبب آلامًا شديدة، والتهابات، وحتى فقدان أسنان ومضاعفات أخرى.

إن المواظبة على زيارة طبيب أسنان بشكل منتظم، وتنظيف الأسنان بشكل دقيق، واستعمال خيط أسنان لتنظيف الأسنان بشكل منتظم ودائم هي طريقة الوقاية الأفضل لمنع التسوّس وتعفّن الأسنان.

مراحل تسوس الأسنان

يحتوي تجويف الفم مثل أعضاء أخرى في الجسم على أنواع عديدة من الجراثيم المختلفة، وبعض هذه الجراثيم ينمو ويتكاثر في بيئة من الأغذية أو المشروبات المختلفة التي تحتوي على السكريات أو النشويات المطبوخة، والتي تُعرف أيضًا باسم الكربوهيدرات المخمّرة (Fermented carbohydrates).

عندما لا يتم إزالة هذه الكربوهيدرات عند تنظيف الأسنان تقوم الجراثيم بتحويلها إلى أحماض في غضو

In [6]:
import pandas as pd
import json

# Charger les données JSON avec encodage utf-8
with open('details_maladies.json', 'r', encoding='utf-8') as fichier_json:
    donnees = json.load(fichier_json)

# Créer un DataFrame
df = pd.DataFrame(donnees)

# Ajouter une colonne vide nommée "score"
df = df.assign(score='')

# Afficher les premières lignes
df.head()


type_maladie                  nom_maladie  \
0  تسوس الأسنان                 تسوس الاسنان   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان  امراض الاغشية المخاطية للفم   
3  تسوس الأسنان         عيوب خلقية لجوف الفم   
4  تسوس الأسنان               ساركوما كابوزي   

                                             contenu score  
0  تسوس الأسنان\nتسوس الاسنان\nتسوس الأسنان هو حا...        
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...        
2  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...        
3  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...        
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...

In [8]:
import pandas as pd
import json

# Définir la fonction score_text
def score_text(text):
    # Définissez ici vos règles de notation
    score = 0
    
    # Mots-clés liés aux symptômes
    symptoms_keywords = ['ألم', 'عرض', 'علامة', 'ظهور', 'تشعر', 'تشعرين', 'يشعر', 'يعاني', 'يعانون', 'يعاني من', 'يعانون من', 'أعراض جانبية', 'تأثيرات جانبية', 'تغييرات في الجسم', 'وظائف غير طبيعية', 'مشاكل صحية', 'انزعاج', 'إزعاج', 'وجه', 'رأس', 'رقبة', 'صدر', 'ظهر', 'بطن', 'ذراع', 'ساق', 'مفصل', 'عضلة', 'جلد', 'شعر', 'أظافر', 'فم', 'لسان', 'أسنان', 'لثة', 'عيون', 'أذنين', 'أنف', 'شديد', 'حاد', 'خفيف', 'متوسط', 'مستمر', 'متقطع', 'مزمن', 'لا يطاق', 'غير محتمل', 'مُنهِك', 'مُؤلم', 'يُعيق', 'يُضعف', 'يُسبب إعاقة', 'حرقة', 'وخز', 'خدر', 'حكة', 'ألم غامض', 'ضعف', 'تشنج', 'غثيان', 'إقياء', 'إسهال', 'إمساك', 'سعال', 'ضيق تنفس', 'صعوبة في البلع', 'دوار', 'إغماء', 'نزيف', 'طفح جلدي', 'احمرار', 'تورم', 'جفاف', 'تقشر', 'تشقق', 'حكة', 'ألم عند اللمس', 'حساسية للمس', 'حساسية للحرارة', 'حساسية للبرودة', 'حساسية للضوء', 'حساسية للصوت', 'فقدان حاسة التذوق', 'فقدان حاسة الشم', 'قلق', 'اكتئاب', 'صداع', 'إرهاق', 'عصبية', 'توتر', 'اضطراب', 'مشاكل في النوم', 'ارتباك', 'تهيج', 'عدوانية', 'هلوسة', 'أوهام', 'فقدان التركيز', 'صعوبة في التفكير', 'صعوبة في اتخاذ القرارات', 'تغييرات في المزاج', 'سلوكيات غير طبيعية', 'ارتفاع درجة الحرارة', 'قشعريرة', 'حمى', 'قشعريرة', 'إفرازات مهبلية غير طبيعية', 'آلام الحوض', 'نزيف بين الدورات', 'نزيف بعد انقطاع الطمث', 'صعوبة التبول', 'إلحاح بولي', 'سلس البول', 'دم في البول', 'إفرازات قطنية بيضاء من المهبل', 'حرقان عند التبول', 'فرط التبول', 'تبول ليلي', 'ضعف الانتصاب', 'قلة الشهية']
    for keyword in symptoms_keywords:
        if keyword in text:
            score += 1
  
    # Mots-clés liés aux causes et aux facteurs de risque
    causes_and_risk_factors_keywords = ['سبب', 'مسبب', 'عامل', 'يسبب', 'يؤدي إلى', 'يزيد من خطر', 'يقلل من خطر', 'مرض', 'عدوى', 'فيروس', 'بكتيريا', 'فطر', 'طفيلي', 'ورم', 'سرطان', 'خلل', 'اضطراب', 'حالة', 'وراثي', 'تاريخ عائلي', 'غذاء', 'تمارين', 'سمنة', 'تدخين', 'كحول', 'مخدرات', 'إجهاد', 'قلة نوم', 'تلوث', 'مواد كيميائية', 'إشعاع', 'لدغة', 'حشرة', 'إصابة', 'حادث', 'كسر', 'جرح', 'عمر', 'عوامل نفسية', 'ضغط عصبي', 'عوامل اجتماعية اقتصادية', 'فقر', 'انعدام الأمن الغذائي', 'إدمان الكحول والمخدرات', 'التعرض للعنف', 'التعرض للسموم', 'عوامل وراثية', 'طفرات جينية', 'عيوب خلقية', 'خلل التوازن الهرموني', 'أمراض المناعة الذاتية', 'استعداد وراثي', 'استهلاك الأدوية', 'التاريخ الطبي الشخصي', 'أمراض سابقة', 'الحمل', 'الرضاعة الطبيعية', 'سن اليأس', 'الجنس', 'العرق', 'النشاط البدني', 'تعرض أشعة الشمس']
    for keyword in causes_and_risk_factors_keywords:
        if keyword in text:
            score += 1
    
    # Mots-clés liés aux complications
    complications_keywords = ['مضاعفات', 'مضاعفة', 'يعقد', 'يؤدي إلى', 'يزيد من خطر', 'إعاقة', 'ضعف', 'فقدان وظيفة', 'اكتئاب', 'قلق', 'ألم مزمن', 'انتشار', 'وفاة', 'يهدد الحياة', 'تلف دائم', 'فشل عضوي', 'غيبوبة', 'عجز دائم', 'تشوهات', 'ندبات', 'التهاب مزمن', 'اضطرابات نفسية', 'اعتمادية على العلاج', 'انتكاس المرض', 'موت الأنسجة', 'نقص المناعة', 'سرطان ثانوي']
    for keyword in complications_keywords:
        if keyword in text:
            score += 1
    
    # Mots-clés liés au diagnostic
    diagnosis_keywords = ['تشخيص', 'تشخيصي', 'يحدد', 'يكشف عن', 'يقيّم', 'تاريخ طبي', 'أعراض', 'فحص جسدي', 'فحص سريري', 'تحليل', 'فحص', 'تصوير', 'أشعة سينية', 'أشعة مقطعية', 'تصوير بالرنين المغناطيسي', 'تحليل دم', 'تحليل بول', 'خزعة', 'تنظير داخلي', 'تخطيط كهربية القلب', 'تخطيط كهربية الدماغ', 'قياس ضغط الدم', 'قياس السكر', 'اختبارات وظائف الكلى', 'اختبارات وظائف الكبد', 'اختبارات الحساسية', 'اختبارات الحمض النووي', 'فحص الحمض النووي', 'فحص جيني']
    for keyword in diagnosis_keywords:
        if keyword in text:
            score += 1
    
    # Keywords related to treatments and drugs
    treatments_and_drugs_keywords = ['علاج', 'علاج طبي', 'دواء', 'جرعة', 'جراحة', 'إشعاع', 'علاج طبيعي', 'علاج إشعاعي', 'علاج كيماوي', 'علاج بالهرمونات', 'علاج بالضوء', 'علاج سلوكي معرفي', 'علاج بالوخز بالإبر', 'علاج بالاسترخاء', 'علاج بالفن', 'علاج بالحمية الغذائية', 'علاج بديل', 'علاج تكميلي', 'جراحة من الحد الأدنى', 'جراحة تنظيرية', 'علاج بالخلايا الجذعية', 'علاج بالجينات', 'العلاج المناعي', 'المضادات الحيوية', 'مضادات الفيروسات', 'مضادات الفطريات', 'مضادات الطفيليات', 'مسكنات الألم', 'خافضات الحرارة', 'مضادات الالتهاب', 'مضادات الا']
    for keyword in treatments_and_drugs_keywords:
        if keyword in text:
            score += 1
    
    # Mots-clés liés aux traitements et aux médicaments
    prevention_keywords = ['الوقاية', 'التوقي', 'الوقاية من', 'التوقي من', 'تجنب', 'تقليل', 'تحسين', 'الحد من', 'الوقاية الأولية', 'التوعية', 'التثقيف', 'التوجيه', 'النصائح', 'التوجيهات', 'التدابير', 'التدابير الوقائية', 'الإجراءات الوقائية', 'تغيير نمط الحياة', 'النظام الغذائي الصحي', 'ممارسة الرياضة', 'تجنب التدخين', 'التقليل من تناول الكحول', 'التقليل من تناول المخدرات', 'النوم الجيد', 'التقليل من التوتر', 'تجنب التعرض للعوامل الملوثة', 'التقليل من التعرض للإشعاع', 'استخدام وسائل الوقاية', 'التطعيم', 'التطهير', 'التعقيم', 'تنظيف اليدين', 'تنظيف البيئة', 'التغذية السليمة', 'العناية بالصحة النفسية', 'التوجيهات الطبية', 'الفحوصات الدورية', 'الكشف المبكر']
    for keyword in prevention_keywords:
        if keyword in text:
            score += 1
    
    return score

# Appliquer la fonction score_text à la colonne « contenu » et mettre à jour la colonne « score »
df['score'] = df['contenu'].apply(score_text)

# Afficher le DataFrame mis à jour
df.head()

type_maladie                  nom_maladie  \
0  تسوس الأسنان                 تسوس الاسنان   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان  امراض الاغشية المخاطية للفم   
3  تسوس الأسنان         عيوب خلقية لجوف الفم   
4  تسوس الأسنان               ساركوما كابوزي   

                                             contenu  score  
0  تسوس الأسنان\nتسوس الاسنان\nتسوس الأسنان هو حا...     31  
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...     37  
2  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...     37  
3  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...     42  
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...     25

In [9]:
def normalize_score(df, column_name):
    # Trouvez les scores minimum et maximum
    min_score = df[column_name].min()
    max_score = df[column_name].max()
    
    # Normalisation des scores entre 0 et 10
    df['score'] = (df[column_name] - min_score) * 10 / (max_score - min_score)
    
    return df

# Exemple d'utilisation :
# En supposant que df est votre DataFrame et que « score » est la colonne contenant les scores
# Remplacez « score » par le nom réel de la colonne dans votre DataFrame
df = normalize_score(df, 'score')
df.head(40)

type_maladie                             nom_maladie  \
0          تسوس الأسنان                            تسوس الاسنان   
1          تسوس الأسنان                       امراض التهاب اللب   
2          تسوس الأسنان             امراض الاغشية المخاطية للفم   
3          تسوس الأسنان                    عيوب خلقية لجوف الفم   
4          تسوس الأسنان                          ساركوما كابوزي   
5              فقر الدم                       ارتفاع الكولسترول   
6          تسوس الأسنان                               جفاف الفم   
7          تسوس الأسنان                              رائحة الفم   
8            مرض السكري                        التهاب البنكرياس   
9         الجهاز الهضمي                          التهاب الكبد ب   
10        الجهاز الهضمي                          القولون العصبي   
11        الجهاز الهضمي                                مرض كرون   
12    ارتفاع الكولسترول                          القلس المترالي   
13        الجهاز الهضمي                         مرض حرقة المعدة   
14        الجهاز الهضمي                          التهاب القولون   
15    ارتفاع الكولسترول                      قصور الصمام الرئوي   
16    ارتفاع الكولسترول                             قلس الابهري   
17    ارتفاع الكولسترول                      تسرع القلب البطيني   
18    ارتفاع الكولسترول                             إحصار القلب   
19        الحمل المنتبذ     التهاب المسالك البولية عديم الاعراض   
20        الحمل المنتبذ                            غياب الإباضة   
21        الحمل المنتبذ                                   العقم   
22           الإنفلونزا                           الفصال العظمي   
23           الإنفلونزا                               حصى الكلى   
24        الجهاز الهضمي  الورمٌ السدويٌ في الجهاز المعدي المعوي   
25        الجهاز الهضمي                          الزحار الاميبي   
26        الجهاز الهضمي                  متلازمة زولينجر إليسون   
27    ارتفاع الكولسترول        شذوذات خلقية في الشرايين التاجية   
28    ارتفاع الكولسترول                      تضيق الثلاثي الشرف   
29           الإنفلونزا          البيلة الجرثومية عديمة الاعراض   
30           الإنفلونزا                               مرض بورغر   
31             الحساسية                  ردة فعل جاريش هركسايمر   
32             الحساسية                             تصلـب الجلد   
33  آلام الدورة الشهرية     الورم الحبيبي اللمفي المنقول جنسيًا   
34        الجهاز الهضمي                             رتق الامعاء   
35    ارتفاع الكولسترول                 الإنعاش القلبي - الرئوي   
36  آلام الدورة الشهرية                           ورم لقمي مسطح   
37  آلام الدورة الشهرية                  الميورة الحالة لليوريا   
38        الجهاز الهضمي                              رتق المريء   
39        الجهاز الهضمي                   فتق السرة عند الاطفال   

                                              contenu     score  
0   تسوس الأسنان\nتسوس الاسنان\nتسوس الأسنان هو حا...  4.461538  
1   تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...  5.384615  
2   تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...  5.384615  
3   تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...  6.153846  
4   تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...  3.538462  
5   فقر الدم\nارتفاع الكولسترول\nالكولسترول (Chole...  2.307692  
6   تسوس الأسنان\nجفاف الفم\nجفاف الفم (Xerostomia...  2.000000  
7   تسوس الأسنان\nرائحة الفم\nيعاني العديد من الأش...  3.384615  
8   مرض السكري\nالتهاب البنكرياس\nيُعد البنكرياس أ...  5.384615  
9   الجهاز الهضمي\nالتهاب الكبد ب\nالتهاب الكبد ب ...  5.230769  
10  الجهاز الهضمي\nالقولون العصبي\nمتلازمة القولون...  5.692308  
11  الجهاز الهضمي\nمرض كرون\nمرض كرون (Crohn's dis...  5.384615  
12  ارتفاع الكولسترول\nالقلس المترالي\nيعد الصمام ...  3.384615  
13  الجهاز الهضمي\nمرض حرقة المعدة\nعندما ينتهي شخ...  3.846154  
14  الجهاز الهضمي\nالتهاب القولون\nالتهاب القولون ...  7.538462  
15  ارتفاع الكولسترول\nقصور الصمام الرئوي\nيقع الص...  3.230769  
16  ارتفاع الكولسترول\nقلس الابهري\nيفصل الصمام ال...  4.615385  
17  ارتفاع الكولسترول\nتسرع القلب البطيني\nتحدث ظا...  3.846154  
18  ارتفا

In [ ]:
import re
import pandas as pd

# Define the function for basic text cleaning
def basic_cleaning(text):
    text = str(text)  # Ensure the input is treated as a string
    text = text.lower()  # Convert text to lowercase
    text = re.sub(r'{.*?}', '', text)  # Remove any CSS code enclosed in curly braces
    text = re.sub(r'[^\w\s\-\+\*/!()\[\]{}<>]', '', text)  # Keep only alphanumeric characters, spaces, and specific symbols
    text = re.sub(r'<[^>]+>', '', text)  # Remove HTML tags
    text = re.sub(r'<style[^>]*>[\s\S]+?</style>', '', text)  # Remove embedded CSS styles
    text = text.replace('\n', ' ')  # Replace newline characters with spaces
    text = re.sub(r'[^\u0621-\u064A0-9\s\-\+\*/!\[\]{}<>]', '', text)  # Remove characters not in Arabic, numbers, or allowed symbols
    text = re.sub(r'\s+', ' ', text).strip()  # Remove extra spaces and trim leading/trailing spaces
    return text

# Fill missing values in the DataFrame with empty strings to avoid errors
df.fillna('', inplace=True)


In [19]:
def tokenize(text):
    return word_tokenize(text)

def remove_stopwords(tokens):
    stop_words = set(stopwords.words('english'))
    return [word for word in tokens if word not in stop_words]

def stem_tokens(tokens):
    stemmer = PorterStemmer()
    return [stemmer.stem(word) for word in tokens]

def lemmatize_tokens(tokens):
    lemmatizer = WordNetLemmatizer()
    return [lemmatizer.lemmatize(word) for word in tokens]

def preprocess_text(df, text_column):
    df['cleaned_text'] = df[text_column].apply(basic_cleaning)
    df['tokens'] = df['cleaned_text'].apply(tokenize)
    df['tokens'] = df['tokens'].apply(remove_stopwords)
    df['stemmed_tokens'] = df['tokens'].apply(lambda x: ' '.join(stem_tokens(x)))
    df['lemmatized_tokens'] = df['tokens'].apply(lambda x: ' '.join(lemmatize_tokens(x)))
    return df

preprocessed_df = preprocess_text(df, 'contenu')
preprocessed_df.head()

type_maladie                  nom_maladie  \
0  تسوس الأسنان                 تسوس الاسنان   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان  امراض الاغشية المخاطية للفم   
3  تسوس الأسنان         عيوب خلقية لجوف الفم   
4  تسوس الأسنان               ساركوما كابوزي   

                                             contenu     score  \
0  تسوس الأسنان\nتسوس الاسنان\nتسوس الأسنان هو حا...  4.461538   
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...  5.384615   
2  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...  5.384615   
3  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...  6.153846   
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...  3.538462   

                                        cleaned_text  \
0  تسوس الأسنان تسوس الاسنان تسوس الأسنان هو حالة...   
1  تسوس الأسنان امراض التهاب اللب قد يكون الالتها...   
2  تسوس الأسنان امراض الاغشية المخاطية للفم تغطي ...   
3  تسوس الأسنان عيوب خلقية لجوف الفم يوجد للفم وظ...   
4  تسوس الأسنان ساركوما كابوزي ساركوما كابوزي عبا...   

                                              tokens  \
0  [تسوس, الأسنان, تسوس, الاسنان, تسوس, الأسنان, ...   
1  [تسوس, الأسنان, امراض, التهاب, اللب, قد, يكون,...   
2  [تسوس, الأسنان, امراض, الاغشية, المخاطية, للفم...   
3  [تسوس, الأسنان, عيوب, خلقية, لجوف, الفم, يوجد,...   
4  [تسوس, الأسنان, ساركوما, كابوزي, ساركوما, كابو...   

                                      stemmed_tokens  \
0  تسوس الأسنان تسوس الاسنان تسوس الأسنان هو حالة...   
1  تسوس الأسنان امراض التهاب اللب قد يكون الالتها...   
2  تسوس الأسنان امراض الاغشية المخاطية للفم تغطي ...   
3  تسوس الأسنان عيوب خلقية لجوف الفم يوجد للفم وظ...   
4  تسوس الأسنان ساركوما كابوزي ساركوما كابوزي عبا...   

                                   lemmatized_tokens  
0  تسوس الأسنان تسوس الاسنان تسوس الأسنان هو حالة...  
1  تسوس الأسنان امراض التهاب اللب قد يكون الالتها...  
2  تسوس الأسنان امراض الاغشية المخاطية للفم تغطي ...  
3  تسوس الأسنان عيوب خلقية لجوف الفم يوجد للفم وظ...  
4  تسوس الأسنان ساركوما كابوزي ساركوما كابوزي عبا...

In [20]:
#importer les bibliothèques pour l'encodage
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from gensim.models import Word2Vec
import numpy as np

In [21]:
print(preprocessed_df['cleaned_text'][983])

الريجيم وتخفيف الوزن نقص البومين الدم إن نقص ألبومين الدم هو حالة تحدث عندما تكون مستويات الألبومين في الدم منخفضة جدا أي أقل من 34 ملليغرام لكل ديسيلتر إذ يعد مستوى الألبومين الطبيعي في الدم هو 34 - 54 ملليغرام لكل ديسيلتر والألبومين هو بروتين تنتجه خلايا الكبد ومن ثم يتم إفرازه إلى الدم بحيث يشكل جزءا كبيرا من بلازما الدم التي هي الجزء السائل من الدم الذي يحتفظ بالبروتينات وخلايا الدم وبما أن الألبومين هو البروتين الرئيس في بلازما الدم فهو يلعب دورا في العديد من الوظائف مثل الحفاظ على الضغط في الأوعية الدموية ونقل المواد عبر الجسم كالهرمونات والأدوية لذلك عندما تكون مستويات الألبومين منخفضة قد لا يتمكن الدم من نقل المواد الأساسية بشكل فعال والجدير بالذكر أنه بوجود نقص ألبومين الدم مع عمل سليم للكبد يقوم الجسم بمعالجة نقص الألبومين في الجسم من خلال زيادة معدل إنتاج الألبومين في الكبد بينما يظهر نقص الألبومين فقط عندما يتجاوز معدل فقدان الألبومين معدل إنتاجه في الكبد أعراض نقص ألبومين الدم ظهور البروتين الزائد في البول عند تحليل البول احتباس السوائل الذي يسبب التورم وخاصة في القدمين أو

In [22]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import tensorflow as tf
from tensorflow.keras.layers import SimpleRNN, Bidirectional, GRU, LSTM, Dense

2024-12-03 22:09:13 [tensorflow] DEBUG: Falling back to TensorFlow client; we recommended you install the Cloud TPU client directly with pip install cloud-tpu-client.
2024-12-03 22:09:15 [h5py._conv] DEBUG: Creating converter from 7 to 5
2024-12-03 22:09:15 [h5py._conv] DEBUG: Creating converter from 5 to 7
2024-12-03 22:09:15 [h5py._conv] DEBUG: Creating converter from 7 to 5
2024-12-03 22:09:15 [h5py._conv] DEBUG: Creating converter from 5 to 7


In [23]:
import pandas as pd
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split

# En supposant que votre DataFrame s'appelle preprocessed_df
# Tokeniser le texte
tokenizer = Tokenizer()
tokenizer.fit_on_texts(preprocessed_df['lemmatized_tokens'])
sequences = tokenizer.texts_to_sequences(preprocessed_df['lemmatized_tokens'])

# Complétez les séquences
max_sequence_length = max([len(seq) for seq in sequences])
X = pad_sequences(sequences, maxlen=max_sequence_length)

# Préparez les étiquettes
y = preprocessed_df['score'].values

# Diviser les données
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [24]:
X_test

array([[   0,    0,    0, ...,  130, 5001, 5789],
       [   0,    0,    0, ..., 3078,  386, 1362],
       [   0,    0,    0, ...,  919,   80, 2425],
       ...,
       [   0,    0,    0, ...,    1, 1806, 3155],
       [   0,    0,    0, ...,    7, 2196,  714],
       [   0,    0,    0, ...,  175,   67, 3208]])

In [25]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, SimpleRNN, Dense

def create_rnn_model(input_shape):
    model = Sequential()
    model.add(Embedding(input_dim=len(tokenizer.word_index) + 1, output_dim=128, input_length=input_shape))
    model.add(SimpleRNN(128))
    model.add(Dense(1, activation='linear'))
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])
    return model

rnn_model = create_rnn_model(X_train.shape[1])
rnn_model.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))


2024-12-03 22:09:35 [py.warnings] WARNING: c:\Users\HP\AppData\Local\Programs\Python\Python312\Lib\site-packages\keras\src\layers\core\embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(



Epoch 1/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 55s 1s/step - loss: 9.3645 - mae: 2.5448 - val_loss: 1.9050 - val_mae: 1.0696
Epoch 2/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 27s 766ms/step - loss: 1.7267 - mae: 1.0231 - val_loss: 1.7787 - val_mae: 1.0115
Epoch 3/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 23s 774ms/step - loss: 1.6478 - mae: 0.9869 - val_loss: 1.7626 - val_mae: 1.0203
Epoch 4/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 22s 761ms/step - loss: 1.2522 - mae: 0.8416 - val_loss: 1.9086 - val_mae: 1.0713
Epoch 5/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 44s 873ms/step - loss: 0.5839 - mae: 0.5552 - val_loss: 1.8055 - val_mae: 1.0440
Epoch 6/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 22s 754ms/step - loss: 0.2425 - mae: 0.3591 - val_loss: 1.8689 - val_mae: 1.0760
Epoch 7/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 22s 753ms/step - loss: 0.1343 - mae: 0.2625 - val_loss: 1.8649 - val_mae: 1.0707
Epoch 8/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 41s 739ms/step - loss: 0.0958 - mae: 0.2191 - val_loss: 1.8603 - val_mae: 1.0761
Epoch 9/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 22s 745ms/ste

In [26]:
from tensorflow.keras.layers import Bidirectional

def create_bidirectional_rnn_model(input_shape):
    model = Sequential()
    model.add(Embedding(input_dim=len(tokenizer.word_index) + 1, output_dim=128, input_length=input_shape))
    model.add(Bidirectional(SimpleRNN(128)))
    model.add(Dense(1, activation='linear'))
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])
    return model

bidirectional_rnn_model = create_bidirectional_rnn_model(X_train.shape[1])
bidirectional_rnn_model.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))


Epoch 1/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 79s 3s/step - loss: 7.4343 - mae: 2.1606 - val_loss: 1.7889 - val_mae: 1.0102
Epoch 2/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 83s 3s/step - loss: 1.7162 - mae: 1.0226 - val_loss: 1.9820 - val_mae: 1.0717
Epoch 3/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 78s 3s/step - loss: 1.6354 - mae: 1.0155 - val_loss: 1.9237 - val_mae: 1.0552
Epoch 4/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 72s 2s/step - loss: 1.4589 - mae: 0.9267 - val_loss: 1.7766 - val_mae: 1.0205
Epoch 5/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 81s 2s/step - loss: 0.9164 - mae: 0.6991 - val_loss: 2.1489 - val_mae: 1.1623
Epoch 6/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 76s 3s/step - loss: 0.4551 - mae: 0.5125 - val_loss: 1.9350 - val_mae: 1.0918
Epoch 7/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 76s 3s/step - loss: 0.1970 - mae: 0.3317 - val_loss: 1.9727 - val_mae: 1.1079
Epoch 8/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 87s 3s/step - loss: 0.1282 - mae: 0.2593 - val_loss: 1.9528 - val_mae: 1.1055
Epoch 9/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 71s 2s/step - loss: 0.0846 - mae: 

In [27]:
from tensorflow.keras.layers import GRU

def create_gru_model(input_shape):
    model = Sequential()
    model.add(Embedding(input_dim=len(tokenizer.word_index) + 1, output_dim=128, input_length=input_shape))
    model.add(GRU(128))
    model.add(Dense(1, activation='linear'))
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])
    return model

gru_model = create_gru_model(X_train.shape[1])
gru_model.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))


Epoch 1/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 78s 3s/step - loss: 14.6501 - mae: 3.4575 - val_loss: 2.4362 - val_mae: 1.2242
Epoch 2/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 67s 2s/step - loss: 1.9513 - mae: 1.0811 - val_loss: 1.5291 - val_mae: 0.9370
Epoch 3/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 57s 2s/step - loss: 0.8906 - mae: 0.7135 - val_loss: 1.4542 - val_mae: 0.9176
Epoch 4/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 60s 2s/step - loss: 0.5542 - mae: 0.5413 - val_loss: 1.3839 - val_mae: 0.8970
Epoch 5/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 95s 3s/step - loss: 0.2243 - mae: 0.3230 - val_loss: 1.4487 - val_mae: 0.9237
Epoch 6/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 72s 2s/step - loss: 0.1455 - mae: 0.2713 - val_loss: 1.4488 - val_mae: 0.9157
Epoch 7/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 69s 2s/step - loss: 0.0795 - mae: 0.2057 - val_loss: 1.4661 - val_mae: 0.9258
Epoch 8/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 79s 3s/step - loss: 0.0720 - mae: 0.1751 - val_loss: 1.4697 - val_mae: 0.9197
Epoch 9/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 83s 3s/step - loss: 0.0591 - mae:

In [28]:
from tensorflow.keras.layers import LSTM

def create_lstm_model(input_shape):
    model = Sequential()
    model.add(Embedding(input_dim=len(tokenizer.word_index) + 1, output_dim=128, input_length=input_shape))
    model.add(LSTM(128))
    model.add(Dense(1, activation='linear'))
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])
    return model

lstm_model = create_lstm_model(X_train.shape[1])
lstm_model.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))


Epoch 1/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 96s 3s/step - loss: 12.4840 - mae: 2.9998 - val_loss: 1.8987 - val_mae: 1.0296
Epoch 2/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 79s 3s/step - loss: 1.6424 - mae: 1.0172 - val_loss: 1.9491 - val_mae: 1.0597
Epoch 3/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 77s 3s/step - loss: 1.7162 - mae: 1.0173 - val_loss: 1.6690 - val_mae: 0.9751
Epoch 4/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 83s 3s/step - loss: 1.4964 - mae: 0.9440 - val_loss: 1.7839 - val_mae: 1.0074
Epoch 5/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 82s 3s/step - loss: 1.0100 - mae: 0.7448 - val_loss: 1.9592 - val_mae: 1.0531
Epoch 6/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 85s 3s/step - loss: 0.7338 - mae: 0.6214 - val_loss: 1.9546 - val_mae: 1.0574
Epoch 7/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 128s 2s/step - loss: 0.4668 - mae: 0.4454 - val_loss: 1.9901 - val_mae: 1.0803
Epoch 8/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 86s 3s/step - loss: 0.2336 - mae: 0.3401 - val_loss: 1.9808 - val_mae: 1.0772
Epoch 9/10
29/29 ━━━━━━━━━━━━━━━━━━━━ 98s 3s/step - loss: 0.1767 - mae

In [29]:
# Définir la fonction pour évaluer les modèles de langage
def evaluate_language_models(models, X_test, y_test):
    evaluation_results = {}
    
    for model_name, model in models.items():
        # Évaluer le modèle à l'aide de mesures standard
        loss, mae = model.evaluate(X_test, y_test)
        evaluation_results[model_name] = {'Loss': loss, 'MAE': mae}
    
    return evaluation_results

# Définissez vos modèles et leurs noms
models = {'Simple RNN': rnn_model, 'Bidirectional RNN': bidirectional_rnn_model, 'GRU': gru_model, 'LSTM': lstm_model}

# Évaluer les modèles de langage
evaluation_results = evaluate_language_models(models, X_test, y_test)

# Imprimer les résultats de l'évaluation
for model_name, metrics in evaluation_results.items():
    print(f"{model_name} - Loss: {metrics['Loss']}, MAE: {metrics['MAE']}")


8/8 ━━━━━━━━━━━━━━━━━━━━ 2s 171ms/step - loss: 2.0195 - mae: 1.1231
8/8 ━━━━━━━━━━━━━━━━━━━━ 3s 310ms/step - loss: 2.0678 - mae: 1.1302
8/8 ━━━━━━━━━━━━━━━━━━━━ 3s 405ms/step - loss: 1.5713 - mae: 0.9396
8/8 ━━━━━━━━━━━━━━━━━━━━ 5s 562ms/step - loss: 2.3744 - mae: 1.1956
Simple RNN - Loss: 1.9107952117919922, MAE: 1.0916622877120972
Bidirectional RNN - Loss: 1.9588148593902588, MAE: 1.1009777784347534
GRU - Loss: 1.4944779872894287, MAE: 0.9303348660469055
LSTM - Loss: 2.1997995376586914, MAE: 1.153064489364624
